In [32]:
# Mengunduh dataset MovieLens 100k
!wget -q https://files.grouplens.org/datasets/movielens/ml-100k.zip
!unzip -q ml-100k.zip

# Mengunduh dataset MovieLens 1M
!wget -q https://files.grouplens.org/datasets/movielens/ml-1m.zip
!unzip -q ml-1m.zip

# Mengunduh dataset MovieLens Metadata
!unzip -q movies_metadata.zip

replace ml-100k/allbut.pl? [y]es, [n]o, [A]ll, [N]one, [r]ename: A
replace ml-1m/movies.dat? [y]es, [n]o, [A]ll, [N]one, [r]ename: A


## Load Dataset Movielens
Dataset ini harus terdiri dari tiga file master yaitu
1. Users yang berisikan user_id, gender, age, occupation, zip_code
2. Movies yang berisikan movie_id, title, genres, is_adult, original_language, original_title, overview, popularity, release_date, revenue, runtime, vote_average, dan vote_count.
3. Ratings yang berisikan user_id, movie_id, rating, dan timestamp

In [177]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split

In [178]:
# Memuat data
ratings = pd.read_csv('ml-100k/u.data', sep='\t', names=['user_id', 'movie_id', 'rating', 'timestamp'])
users = pd.read_csv('ml-100k/u.user', sep='|', names=['user_id', 'gender', 'age', 'occupation', 'zip_code'])
movies = pd.read_csv('ml-100k/u.item', sep='|', encoding='ISO-8859-1', header=None, names=['movie_id', 'title', 'release_date', 'imdb_url'], usecols=[0,1,2,4])

In [179]:
# Memuat data
ml1_movies = pd.read_csv('ml-1m/movies.dat', sep='::', encoding='ISO-8859-1', header=None, names=['movie_id', 'title', 'genres'], usecols=[0,1,2])
ml1_movies.head(1)

<ipython-input-179-e71d00712615>:2: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  ml1_movies = pd.read_csv('ml-1m/movies.dat', sep='::', encoding='ISO-8859-1', header=None, names=['movie_id', 'title', 'genres'], usecols=[0,1,2])


movie_id             title                       genres
0         1  Toy Story (1995)  Animation|Children's|Comedy

In [180]:
# Menggabungkan kolom 'genres' dari ml1_movies ke movies berdasarkan 'movie_id'
movies = movies.merge(ml1_movies[['movie_id', 'genres']], on='movie_id', how='left')
# Extract year from title
movies[["title", "year"]] = movies["title"].str.extract('(.*)\((\d+)\)')
# Remove trailing whitespace from title
movies["title"] = movies["title"].str.strip()
ml1_movies = ml1_movies.iloc[0:0]

In [181]:
ml_meta_movies = pd.read_csv('movies_metadata.csv', low_memory=False)
ml_meta_movies.head(1)

adult                              belongs_to_collection    budget  \
0  False  {'id': 10194, 'name': 'Toy Story Collection', ...  30000000   

                                              genres  \
0  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...   

                               homepage   id    imdb_id original_language  \
0  http://toystory.disney.com/toy-story  862  tt0114709                en   

  original_title                                           overview  ...  \
0      Toy Story  Led by Woody, Andy's toys live happily in his ...  ...   

  release_date      revenue runtime                          spoken_languages  \
0   1995-10-30  373554033.0    81.0  [{'iso_639_1': 'en', 'name': 'English'}]   

     status  tagline      title  video vote_average vote_count  
0  Released      NaN  Toy Story  False          7.7     5415.0  

[1 rows x 24 columns]

In [182]:
print(movies["movie_id"].nunique())
print(users["user_id"].nunique())

1682
943


In [183]:
# prompt: i wanna check that all title on dataframe movies is exists on dataframe ml_meta_movies with column title or original_title and how many title is not exists, with text is lowercase, and remove the row on movies if is not exists.

# Convert titles to lowercase for comparison
movies['title_lower'] = movies['title'].str.lower()
ml_meta_movies['title_lower'] = ml_meta_movies['title'].str.lower()
ml_meta_movies['original_title_lower'] = ml_meta_movies['original_title'].str.lower()

# Check which titles in 'movies' exist in 'ml_meta_movies'
movies_exist = movies['title_lower'].isin(ml_meta_movies['title_lower']) | movies['title_lower'].isin(ml_meta_movies['original_title_lower'])

# Count how many titles don't exist
not_exist_count = (~movies_exist).sum()
print("Number of titles not existing in ml_meta_movies:", not_exist_count)

# Remove rows from 'movies' where titles don't exist
movies = movies[movies_exist]

# Drop the temporary lowercase title columns
movies = movies.drop(['title_lower'], axis=1)
ml_meta_movies = ml_meta_movies.drop(['title_lower', 'original_title_lower'], axis=1)
movies.reset_index(drop=True, inplace=True)

Number of titles not existing in ml_meta_movies: 518


In [184]:
# prompt: remove all rows on ratings dataframe if the column movie_id is not exists on movies dataframe

# Filter ratings DataFrame based on movie existence
ratings = ratings[ratings['movie_id'].isin(movies['movie_id'])]
ratings.reset_index(drop=True, inplace=True)

In [185]:
# prompt: Can you reset movie_id column on movies datafram start to 1 and syncronize to movie_id on ratings dataframe

# Create a mapping of old movie_id to new movie_id
movie_id_map = {old_id: new_id for new_id, old_id in enumerate(movies['movie_id'].unique(), start=1)}

# Apply the mapping to the movies DataFrame
movies['movie_id'] = movies['movie_id'].map(movie_id_map)

# Apply the mapping to the ratings DataFrame
ratings['movie_id'] = ratings['movie_id'].map(movie_id_map)

<ipython-input-185-05ef1c64b40f>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ratings['movie_id'] = ratings['movie_id'].map(movie_id_map)


In [186]:
# prompt: Can you reset user_id column on ratings datafram start to 1 and syncronize to user_id on users dataframe and remove all rows on users when the user_id is not exist on unique user_id on ratings

# Get unique user_ids from ratings
unique_rating_users = ratings['user_id'].unique()

# Filter users DataFrame to keep only users present in ratings
users = users[users['user_id'].isin(unique_rating_users)]
users.reset_index(drop=True, inplace=True)

# Create a mapping of old user_id to new user_id
user_id_map = {old_id: new_id for new_id, old_id in enumerate(users['user_id'].unique(), start=1)}

# Apply the mapping to the users DataFrame
users['user_id'] = users['user_id'].map(user_id_map)

# Apply the mapping to the ratings DataFrame
ratings['user_id'] = ratings['user_id'].map(user_id_map)


<ipython-input-186-63a67bcdbf80>:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ratings['user_id'] = ratings['user_id'].map(user_id_map)


In [187]:
# prompt: Now i want to copy columns adult, original_language, original_title, overview, popularity, release_date, revenue, runtime, vote_average, dan vote_count from ml_meta_movies to movies dataframe based on title or original_title

# Create temporary lowercase title columns for efficient comparison
movies['title_lower'] = movies['title'].str.lower()
ml_meta_movies['title_lower'] = ml_meta_movies['title'].str.lower()
ml_meta_movies['original_title_lower'] = ml_meta_movies['original_title'].str.lower()

# Initialize new columns in 'movies' DataFrame
movies['adult'] = None
movies['original_language'] = None
movies['original_title'] = None
movies['overview'] = None
movies['popularity'] = None
movies['release_date'] = None
movies['revenue'] = None
movies['runtime'] = None
movies['vote_average'] = None
movies['vote_count'] = None

# Iterate over 'movies' and copy data from 'ml_meta_movies'
for index, row in movies.iterrows():
    title_lower = row['title_lower']
    match = ml_meta_movies[(ml_meta_movies['title_lower'] == title_lower) | (ml_meta_movies['original_title_lower'] == title_lower)]
    if not match.empty:
        movies.loc[index, 'adult'] = match['adult'].iloc[0]
        movies.loc[index, 'original_language'] = match['original_language'].iloc[0]
        movies.loc[index, 'original_title'] = match['original_title'].iloc[0]
        movies.loc[index, 'overview'] = match['overview'].iloc[0]
        movies.loc[index, 'popularity'] = match['popularity'].iloc[0]
        movies.loc[index, 'release_date'] = match['release_date'].iloc[0]
        movies.loc[index, 'revenue'] = match['revenue'].iloc[0]
        movies.loc[index, 'runtime'] = match['runtime'].iloc[0]
        movies.loc[index, 'vote_average'] = match['vote_average'].iloc[0]
        movies.loc[index, 'vote_count'] = match['vote_count'].iloc[0]

# Drop the temporary lowercase title columns
movies = movies.drop(['title_lower'], axis=1)
ml_meta_movies = ml_meta_movies.drop(['title_lower', 'original_title_lower'], axis=1)


## Show Tables

In [188]:
# Ratings
ratings.head(1)

user_id  movie_id  rating  timestamp
0      196       169       3  881250949

In [189]:
# Users
users.head(1)

user_id  gender age  occupation zip_code
0        1      24   M  technician    85711

In [190]:
# Movies
movies.head(1)

movie_id      title release_date  \
0         1  Toy Story   1995-10-30   

                                            imdb_url  \
0  http://us.imdb.com/M/title-exact?Toy%20Story%2...   

                        genres  year  adult original_language original_title  \
0  Animation|Children's|Comedy  1995  False                en      Toy Story   

                                            overview popularity      revenue  \
0  Led by Woody, Andy's toys live happily in his ...  21.946943  373554033.0   

  runtime vote_average vote_count  
0    81.0          7.7     5415.0

## Sample Recsys to check dataset is valid for embedding or not

In [191]:
# Memuat data
data = ratings.copy()
data = data[['user_id', 'movie_id', 'rating']]

# Normalisasi ID pengguna dan item (karena ID asli mungkin tidak dimulai dari 0)
data['user_id'] = data['user_id'] - 1
data['movie_id'] = data['movie_id'] - 1

# Melihat statistik dataset
num_users = data['user_id'].nunique()
num_items = data['movie_id'].nunique()
print(f"Number of users: {num_users}, Number of items: {num_items}")

# Split dataset menjadi train dan test
train_data, test_data = train_test_split(data, test_size=0.2, random_state=42)

Number of users: 943, Number of items: 1164


In [192]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, Dataset

class MovieLensDataset(Dataset):
    def __init__(self, data):
        self.user_ids = torch.tensor(data['user_id'].values, dtype=torch.long)
        self.item_ids = torch.tensor(data['movie_id'].values, dtype=torch.long)
        self.ratings = torch.tensor(data['rating'].values, dtype=torch.float32)

    def __len__(self):
        return len(self.ratings)

    def __getitem__(self, idx):
        return self.user_ids[idx], self.item_ids[idx], self.ratings[idx]

class MFModel(nn.Module):
    def __init__(self, num_users, num_items, embedding_size):
        super(MFModel, self).__init__()
        self.user_embedding = nn.Embedding(num_users, embedding_size)
        self.item_embedding = nn.Embedding(num_items, embedding_size)

    def forward(self, user_id, item_id):
        user_vec = self.user_embedding(user_id)
        item_vec = self.item_embedding(item_id)
        dot_product = torch.sum(user_vec * item_vec, dim=1)
        return dot_product

    def regularization_loss(self):
        return self.reg_factor * (torch.norm(self.user_embedding.weight) + torch.norm(self.item_embedding.weight))

In [193]:
# DataLoader untuk training
train_dataset = MovieLensDataset(train_data)
train_loader = DataLoader(train_dataset, batch_size=256, shuffle=True)

# Hyperparameters
embedding_size = 30
reg_factor = 0.01
model = MFModel(num_users, num_items, embedding_size)
criterion = nn.MSELoss()
optimizer = optim.Adam(model.parameters(), lr=0.01)

# Training loop
for epoch in range(10):
    model.train()
    total_loss = 0
    for data_user_id, data_item_id, data_rating in train_loader:
        optimizer.zero_grad()
        predictions = model(data_user_id, data_item_id)
        loss = criterion(predictions, data_rating)
        loss.backward()
        optimizer.step()
        total_loss += loss.item()
    print(f"Epoch {epoch+1}, Loss: {total_loss/len(train_loader):.4f}")

Epoch 1, Loss: 34.7072
Epoch 2, Loss: 18.3940
Epoch 3, Loss: 9.6635
Epoch 4, Loss: 4.3265
Epoch 5, Loss: 2.3596
Epoch 6, Loss: 1.5818
Epoch 7, Loss: 1.1944
Epoch 8, Loss: 0.9714
Epoch 9, Loss: 0.8330
Epoch 10, Loss: 0.7384


In [194]:
from sklearn.metrics import mean_squared_error
import numpy as np

model.eval()
test_dataset = MovieLensDataset(test_data)
test_loader = DataLoader(test_dataset, batch_size=256, shuffle=False)

predictions, targets = [], []
with torch.no_grad():
    for data_user_id, data_item_id, data_rating in test_loader:
        output = model(data_user_id, data_item_id)
        predictions.extend(output.numpy())
        targets.extend(data_rating.numpy())

rmse = np.sqrt(mean_squared_error(targets, predictions))
print(f"Test RMSE: {rmse:.4f}")

Test RMSE: 1.8248


In [195]:
def get_top_n_recommendations_pytorch(model, user_id, N=10):
    # Dapatkan semua item yang tersedia
    all_items = np.array(range(num_items))

    # Cek item yang sudah dirating oleh user
    rated_items = train_data[train_data['user_id'] == user_id]['movie_id'].values

    # Ambil item yang belum dirating oleh user
    items_to_predict = np.setdiff1d(all_items, rated_items)

    # Prediksi rating untuk item-item tersebut
    model.eval()
    with torch.no_grad():
        user_ids = torch.tensor([user_id] * len(items_to_predict))
        item_ids = torch.tensor(items_to_predict)
        predicted_ratings = model(user_ids, item_ids).numpy()

    # Urutkan item berdasarkan rating tertinggi
    top_n_items = items_to_predict[np.argsort(predicted_ratings)[-N:][::-1]]

    return top_n_items

# Contoh penggunaan
user_id = 0
top_n_recommendations = get_top_n_recommendations_pytorch(model, user_id, N=10)
print(f"Top 10 recommended items for user {user_id}: {top_n_recommendations}")

Top 10 recommended items for user 0: [1151  916  718 1134  832  941  327  347  631  434]


## Export the datasets


In [196]:
ratings.to_csv(f"ratings.csv", index=False)
movies.to_csv(f"movies.csv", index=False)
users.to_csv(f"users.csv", index=False)